In [1]:
import cv2
import numpy as np
from google.colab.patches import cv2_imshow

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [48]:
#Rutas de las imágenes
image2_path = '/content/drive/MyDrive/Visión por computadora/Tareas/Clase_6/Imagen de WhatsApp 2024-04-18 a las 16.36.52_c5c212e8.jpg'
image1_path = '/content/drive/MyDrive/Visión por computadora/Tareas/Clase_6/Imagen de WhatsApp 2024-04-18 a las 16.36.56_abe06ab4.jpg'

In [49]:
#Cargar las imágenes
image1 = cv2.imread(image1_path)
image2 = cv2.imread(image2_path)

In [50]:
#Convertir las imágenes a escala de grises
gray_image1 = cv2.cvtColor(image1, cv2.COLOR_BGR2GRAY)
gray_image2 = cv2.cvtColor(image2, cv2.COLOR_BGR2GRAY)

In [51]:
#Inicializar el detector ORB
orb = cv2.ORB_create()

In [52]:
#Encontrar los puntos clave y descriptores en ambas imágenes
keypoints1, descriptors1 = orb.detectAndCompute(gray_image1, None)
keypoints2, descriptors2 = orb.detectAndCompute(gray_image2, None)


In [53]:
#Emparejar los descriptores utilizando BFMatcher
bf = cv2.BFMatcher(cv2.NORM_HAMMING, crossCheck=True)
matches = bf.match(descriptors1, descriptors2)

In [54]:
#Ordenar los emparejamientos basados en su distancia
matches = sorted(matches, key = lambda x:x.distance)

In [55]:
#Seleccionar las mejores coincidencias
good_matches = matches[:50]

In [56]:
#Extraer las ubicaciones de los puntos clave en ambas imágenes
points1 = np.float32([keypoints1[match.queryIdx].pt for match in good_matches]).reshape(-1, 1, 2)
points2 = np.float32([keypoints2[match.trainIdx].pt for match in good_matches]).reshape(-1, 1, 2)

In [57]:
#Calcular la homografía entre las dos imágenes
homography, _ = cv2.findHomography(points1, points2, cv2.RANSAC)

In [58]:
#Aplicar la homografía a la primera imagen
panorama = cv2.warpPerspective(image1, homography, (image1.shape[1] + image2.shape[1], image1.shape[0]))

In [59]:
#Superponer la segunda imagen en el panorama
panorama[:image2.shape[0], :image2.shape[1]] = image2

In [60]:
#Mostrar el resultado
cv2_imshow(panorama)

Output hidden; open in https://colab.research.google.com to view.

In [64]:
comparison = cv2.hconcat([image1, image2, panorama])

In [65]:
#Mostrar la comparación
cv2_imshow(comparison)